In [1]:
%pip install pygame

Note: you may need to restart the kernel to use updated packages.


In [2]:
import numpy as np
from tensorflow import keras
import matplotlib.pyplot as plt
import time
import random
import collections

In [3]:
import pygame
import time
import random

 
white = (255, 255, 255)
yellow = (255, 255, 102)
black = (0, 0, 0)
red = (213, 50, 80)
green = (0, 255, 0)
blue = (50, 153, 213)
 
dis_width = 600
dis_height = 400
 

 
 
def Your_score(score, dis, score_font):
    value = score_font.render("Your Score: " + str(score), True, yellow)
    dis.blit(value, [0, 0])
 
 
 
def our_snake(snake_block, snake_list, dis):
    for x in snake_list:
        pygame.draw.rect(dis, black, [x[0], x[1], snake_block, snake_block])
 
 
 
def gameLoop(agent):
    pygame.init()
    font_style = pygame.font.SysFont("bahnschrift", 25)
    score_font = pygame.font.SysFont("comicsansms", 35)
    dis = pygame.display.set_mode((dis_width, dis_height))
    pygame.display.set_caption('Snake Game by Edureka')

    clock = pygame.time.Clock()

    snake_block = 10
    snake_speed = 15


    game_over = False
    game_close = False
 
    x1 = dis_width / 2
    y1 = dis_height / 2
 
    x1_change = 0
    y1_change = 0
 
    snake_List = []
    Length_of_snake = 1
    score=-1
    foodx = round(random.randrange(0, dis_width - snake_block) / 10.0) * 10.0
    foody = round(random.randrange(0, dis_height - snake_block) / 10.0) * 10.0
    episodeLoss=0
    while not game_over and Length_of_snake-1<50:
        state=[x1, y1, foodx, foody]
        score=score+1
        reward=0
        action=agent.select(state)
        
        if action == 0:
                    x1_change = -snake_block
                    y1_change = 0
        elif action == 1:
                    x1_change = snake_block
                    y1_change = 0
        elif action == 2:
                    y1_change = -snake_block
                    x1_change = 0
        elif action == 3:
                    y1_change = snake_block
                    x1_change = 0
 
        if x1 >= dis_width or x1 < 0 or y1 >= dis_height or y1 < 0:
            game_over = True
            reward=-80
        x1 += x1_change
        y1 += y1_change
        dis.fill(blue)
        pygame.draw.rect(dis, green, [foodx, foody, snake_block, snake_block])
        snake_Head = []
        snake_Head.append(x1)
        snake_Head.append(y1)
        snake_List.append(snake_Head)
        if len(snake_List) > Length_of_snake:
            del snake_List[0]
 
        for x in snake_List[:-1]:
            if x == snake_Head:
                game_over = True
                reward=-80
 
        our_snake(snake_block, snake_List, dis)
        Your_score(Length_of_snake - 1, dis, score_font)
 
        
        
        if x1 == foodx and y1 == foody:
            foodx = round(random.randrange(0, dis_width - snake_block) / 10.0) * 10.0
            foody = round(random.randrange(0, dis_height - snake_block) / 10.0) * 10.0
            Length_of_snake += 1
            reward=30
        state_next=[x1,y1,foodx,foody]
        terminal_state=game_over or (Length_of_snake-1>=50)
        loss=agent.learn()
        pygame.display.update()
        if loss!=None:
            episodeLoss+=loss
        agent.remember(state, action, reward, state_next, terminal_state)
        clock.tick(snake_speed)
        score=score+reward
        #time.sleep(5)
    ##End while game_over
    pygame.quit()
    return score, episodeLoss
 

pygame 2.1.2 (SDL 2.0.18, Python 3.9.7)
Hello from the pygame community. https://www.pygame.org/contribute.html


In [4]:
GAMMA = 0.985
MEMORY_SIZE = 10000
LEARNING_RATE = 0.001
BATCH_SIZE = 64
EXPLORATION_MAX = 1.0
EXPLORATION_MIN = 0.02
EXPLORATION_DECAY = 0.98
NUMBER_OF_EPISODES = 400
MAX_STEPS = 200
ACTUALIZE= 1500

# Creación de la Replay Memory
Buffer circular en el que se almacenan resultados previos, que serán empleados en la fase learn del algoritmo

In [5]:
class ReplayMemory:

    def __init__(self,number_of_observations):
        # Create replay memory
        self.states = np.zeros((MEMORY_SIZE, number_of_observations))
        self.states_next = np.zeros((MEMORY_SIZE, number_of_observations))
        self.actions = np.zeros(MEMORY_SIZE, dtype=np.int32)
        self.rewards = np.zeros(MEMORY_SIZE)
        self.terminal_states = np.zeros(MEMORY_SIZE, dtype=bool)
        self.size=0

    def store_transition(self, state, action, reward, state_next, terminal_state):
        # Store a transition (s,a,r,s') in the replay memory
        i = self.size
        self.states[i%MEMORY_SIZE] = state
        self.states_next[i%MEMORY_SIZE] = state_next
        self.actions[i%MEMORY_SIZE] = action
        self.rewards[i%MEMORY_SIZE] = reward
        self.terminal_states[i%MEMORY_SIZE] = terminal_state
        self.size += 1

    def sample_memory(self, batch_size):
        # Generate a sample of transitions from the replay memory
        batch = np.random.choice(min(MEMORY_SIZE, self.size), batch_size)
        states = self.states[batch]
        states_next = self.states_next[batch]
        rewards = self.rewards[batch]
        actions = self.actions[batch]   
        terminal_states = self.terminal_states[batch]  
        return states, actions, rewards, states_next, terminal_states

# DQN
Clase que maneja toda la parte de la Deep Q neural network

In [6]:
class DQN:

    def __init__(self, number_of_observations, number_of_actions):
        # Initialize variables and create neural model
        self.exploration_rate = EXPLORATION_MAX
        self.number_of_actions = number_of_actions
        self.number_of_observations = number_of_observations
        self.scores = []
        self.avg_scores=[]
        self.loss=[]
        self.avg_loss=[]
        self.memory = ReplayMemory(number_of_observations)
        #Q network
        self.model = keras.models.Sequential()

        self.model.add(keras.layers.Dense(500, input_shape=(number_of_observations,), \
                             activation="relu",kernel_initializer="he_normal"))
        self.model.add(keras.layers.Dense(250, activation="relu",kernel_initializer="he_normal"))
        self.model.add(keras.layers.Dense(100, activation="relu",kernel_initializer="he_normal"))
        self.model.add(keras.layers.Dense(number_of_actions, activation="linear"))

        self.model.compile(loss="mse", optimizer=keras.optimizers.Adam(learning_rate=LEARNING_RATE))
        #target network
        self.target_net = keras.models.Sequential()

        self.target_net.add(keras.layers.Dense(500, input_shape=(number_of_observations,), \
                             activation="relu",kernel_initializer="he_normal"))
        self.target_net.add(keras.layers.Dense(250, activation="relu",kernel_initializer="he_normal"))
        self.target_net.add(keras.layers.Dense(100, activation="relu",kernel_initializer="he_normal"))
        self.target_net.add(keras.layers.Dense(number_of_actions, activation="linear"))

        self.target_net.compile(loss="mse", optimizer=keras.optimizers.Adam(learning_rate=LEARNING_RATE))
        self.actualize_target()


    def remember(self, state, action, reward, next_state, terminal_state):
        # Store a tuple (s, a, r, s') for experience replay
        state = np.reshape(state, [1, self.number_of_observations])
        next_state = np.reshape(next_state, [1, self.number_of_observations])
        self.memory.store_transition(state, action, reward, next_state, terminal_state)

    def select(self, state):
        # Generate an action for a given state using epsilon-greedy policy
        if np.random.rand() < self.exploration_rate:
            return random.randrange(self.number_of_actions)
        else:
            state = np.reshape(state, [1, self.number_of_observations])
            q_values = self.model.predict(state)
            return np.argmax(q_values[0])

    def learn(self):
        # Learn the value Q using a sample of examples from the replay memory
        if self.memory.size < BATCH_SIZE: return

        states, actions, rewards, next_states, terminal_states = self.memory.sample_memory(BATCH_SIZE)

        q_targets = self.model.predict(states)
        q_next_states = self.target_net.predict(next_states)
        for i in range(BATCH_SIZE):
             if (terminal_states[i]):
                  q_targets[i][actions[i]] = rewards[i]
             else:
                  q_targets[i][actions[i]] = rewards[i] + GAMMA * np.max(q_next_states[i])    

        loss=self.model.train_on_batch(states, q_targets)
        return loss
        # Decrease exploration rate
        #self.exploration_rate *= EXPLORATION_DECAY
        #self.exploration_rate = max(EXPLORATION_MIN, self.exploration_rate)

    def decayExploration(self, score):
        self.exploration_rate *= EXPLORATION_DECAY
        self.exploration_rate = max(EXPLORATION_MIN, self.exploration_rate)

    def add_score(self, score, avg_scores, loss, avg_loss):
       # Add the obtained score in a list to be presented later
        self.scores.append(score)
        self.avg_scores.append(avg_scores)
        self.loss.append(loss)
        self.avg_loss.append(avg_loss)

    def display_scores_graphically(self):
        # Display the obtained scores graphically
        plt.plot(self.scores)
        plt.xlabel("Episode")
        plt.ylabel("Score")
        plt.show()

        plt.plot(self.avg_scores)
        plt.xlabel("Episode")
        plt.ylabel("Avg Score")
        plt.show()

        plt.plot(self.loss)
        plt.xlabel("Episode")
        plt.ylabel("Loss")
        plt.show()

        plt.plot(self.avg_loss)
        plt.xlabel("Episode")
        plt.ylabel("Avg Loss")
        plt.show()

    def actualize_target(self):
        for i in range(len(self.model.layers)):
          weights=self.model.get_layer(index=i).get_weights()
          layer=self.target_net.get_layer(index=i)
          layer.set_weights(weights)

# Entorno del problema
## Vector de estados:
    state[0]=Snake x
    state[1]=Snake y
    state[2]=Food x
    state[3]=Food y
    
## Acciones
    0 ir arriba
    1 ir derecha
    2 ir abajo
    3 ir izquierda

## Recompensas
 ### Recompensas positivas:
     +100 por comer la comida
 ### Recompensas negativas:
     -Distancia a la comida, penalizar alejarse de la comida, para intentar crear el comportamiente de ir a por comida

## Condiciones de finalización:
    Chocarse con el borde
    Chocarse con su propio cuerpo
    Comer 50 comidas sin morir

In [7]:


ACTUALIZE=20
num_episodes=200

In [ ]:
numberObservations=4
numberActions=4

episode=0
goal=False
last_scores=np.zeros(100)
last_loss=np.zeros(100)
start_time = time.perf_counter()
agent = DQN(numberObservations, numberActions)
while (episode<num_episodes) and not(goal):
    score, loss= gameLoop(agent)
    last_scores[(episode-1)%100]=score
    last_loss[(episode-1)%100]=loss
    avg_score=np.mean(last_scores[:min(100, episode)])
    avg_loss=np.mean(last_loss[:min(100, episode)])
    agent.add_score(score, avg_score, loss, avg_loss)
    print("Episode {0:>3}: ".format(episode), end = '')
    print("score {0:>3} ".format(score), end = '')
    print("avg_score {0:>3} ".format(avg_score), end = '')
    print("loss {0:>3}: ".format(loss), end='')
    print("avg_loss {0:>3}: ".format(avg_loss), end='')
    print("(exploration rate: %.2f, " % agent.exploration_rate, end = '')
    print("transitions: " + str(agent.memory.size) + ")")
    episode+=1
    if episode%ACTUALIZE==0:
          agent.actualize_target()

2/2 [==============================] - 0s 3ms/step


2/2 [==============================] - 0s 2ms/step


2/2 [==============================] - 0s 2ms/step


2/2 [==============================] - 0s 2ms/step


2/2 [==============================] - 0s 2ms/step


...

2/2 [==============================] - 0s 118ms/step


2/2 [==============================] - 0s 123ms/step


2/2 [==============================] - 0s 130ms/step


2/2 [==============================] - 0s 123ms/step


2/2 [==============================] - 0s 134ms/step
